In [1]:
import numpy as np
import optuna
from optuna.visualization import plot_param_importances, plot_contour
import matplotlib.pyplot as plt

# Załóżmy, że masz już zaimportowane klasy:
# from your_module import TSPProblem, DualPheromoneACO, PheromoneConfig, ExplorationConfig, ExplorationDecayType
from tsp_problem import TSPProblem
from dual_pheromone_tsp import DualPheromoneACO, PheromoneConfig, ExplorationConfig, ExplorationDecayType

def objective(trial):
    """Funkcja celu dla optymalizacji Optuna"""

    # Stały seed dla reproducibility
    np.random.seed(42)
    coords = np.random.rand(50, 2)  # 50 punktów zamiast 150

    # Sugerowane parametry przez Optuna
    n_ants = trial.suggest_int('n_ants', 10, 100)
    n_iterations = int(5000 / n_ants)  # Zależność od n_ants

    pheromone_reward_factor = trial.suggest_float('pheromone_reward_factor', 1, 1000)
    negative_pheromone_scaling = trial.suggest_float('negative_pheromone_scaling', 0.001, 1)

    initial_rate = trial.suggest_float('initial_rate', 0, 0.4)

    alpha = trial.suggest_float('alpha', 0.1, 5.0)
    beta = trial.suggest_float('beta', 0.1, 5.0)
    gamma = trial.suggest_float('gamma', 0.1, 5.0)

    rho_pos = trial.suggest_float('rho_pos', 0.01, 0.5)
    rho_neg = trial.suggest_float('rho_neg', 0.01, 0.5)

    # n_reinforce musi być mniejsze niż n_ants/2
    max_reinforce = min(25, int(n_ants // 2))
    if max_reinforce < 2:
        max_reinforce = 2
    n_reinforce = trial.suggest_int('n_reinforce', 2, max_reinforce)

    elite_boost = trial.suggest_categorical('elite_boost', [True, False])

    try:
        # Tworzenie problemu TSP
        problem = TSPProblem(coords)

        # Konfiguracja feromonów
        pheromone_config = PheromoneConfig(
            min_pheromone=1e-6,  # Stała wartość
            pheromone_reward_factor=pheromone_reward_factor,
            negative_pheromone_scaling=negative_pheromone_scaling
        )

        # Konfiguracja eksploracji
        exploration_config = ExplorationConfig(
            initial_rate=initial_rate,
            final_rate=0.0,  # Stała wartość
            decay_type=ExplorationDecayType.LINEAR  # Stała wartość
        )

        # Tworzenie algorytmu ACO
        dual_aco = DualPheromoneACO(
            problem=problem,
            n_ants=n_ants,
            n_iterations=n_iterations,
            alpha=alpha,
            beta=beta,
            gamma=gamma,
            rho_pos=rho_pos,
            rho_neg=rho_neg,
            n_reinforce=n_reinforce,
            elite_boost=elite_boost,
            pheromone_config=pheromone_config,
            exploration_config=exploration_config,
        )

        # Inicjalizacja i uruchomienie
        dual_aco.init_progress()

        while not dual_aco.stopping_condition_is_met():
            dual_aco.step()
            dual_aco.update_progress()

        # Zwracamy długość najlepszej trasy (minimalizujemy)
        best_result = dual_aco.result()
        return best_result.objectives[0]

    except Exception as e:
        print(f"Error in trial: {e}")
        # Zwracamy wysoką wartość w przypadku błędu
        return float('inf')

def run_optimization():
    """Uruchamia optymalizację hiperparametrów"""

    # Tworzenie studium Optuna
    study = optuna.create_study(
        direction='minimize',  # Minimalizujemy długość trasy
        study_name='TSP_Hyperparameter_Optimization'
    )

    print("Rozpoczynam optymalizację hiperparametrów...")
    print("Liczba prób: 100")
    print("Problem: TSP z 50 punktami")

    # Uruchomienie optymalizacji
    study.optimize(objective, n_trials=100, show_progress_bar=True)

    # Wyświetlenie wyników
    print("\n" + "="*50)
    print("WYNIKI OPTYMALIZACJI")
    print("="*50)

    print(f"Najlepsza wartość: {study.best_value:.6f}")
    print(f"Najlepsze parametry:")
    for param, value in study.best_params.items():
        print(f"  {param}: {value}")

    # Statystyki prób
    print(f"\nLiczba zakończonych prób: {len(study.trials)}")
    print(f"Liczba prób z błędami: {len([t for t in study.trials if t.state == optuna.trial.TrialState.FAIL])}")

    return study

def create_visualizations(study):
    """Tworzy wykresy analizy parametrów"""

    print("\nTworzenie wykresów...")

    # Wykres ważności parametrów
    fig1 = plot_param_importances(study)
    fig1.update_layout(
        title="Ważność hiperparametrów",
        title_x=0.5,
        width=1800,
        height=1600
    )
    fig1.show()

    # Wykres konturowy dla najważniejszych parametrów
    # Automatycznie wybierze 2 najważniejsze parametry
    try:
        fig2 = plot_contour(study)
        fig2.update_layout(
            title="Wykres konturowy najważniejszych parametrów",
            title_x=0.5,
            width=1800,
            height=1600
        )
        fig2.show()
    except ValueError as e:
        print(f"Nie można utworzyć wykresu konturowego: {e}")
        print("Spróbuj określić konkretne parametry dla wykresu konturowego.")

    # Możesz też utworzyć konkretny wykres konturowy dla wybranych parametrów:
    # fig3 = plot_contour(study, params=['alpha', 'beta'])
    # fig3.show()

def analyze_results(study):
    """Dodatkowa analiza wyników"""

    print("\n" + "="*50)
    print("DODATKOWA ANALIZA")
    print("="*50)

    # Top 10 najlepszych prób
    trials_df = study.trials_dataframe()
    top_trials = trials_df.nsmallest(10, 'value')

    print("Top 10 najlepszych wyników:")
    print(top_trials[['number', 'value']].to_string(index=False))

    # Korelacje parametrów z wynikami
    print(f"\nKorelacje parametrów z wartością celu:")
    correlations = trials_df.corr()['value'].sort_values(key=abs, ascending=False)
    for param, corr in correlations.items():
        if param != 'value' and not param.startswith('datetime') and not param.startswith('duration'):
            print(f"  {param}: {corr:.4f}")


In [2]:
study = run_optimization()
create_visualizations(study)
analyze_results(study)

print(f"\nAnaliza zakończona! Najlepszy wynik: {study.best_value:.6f}")

[I 2025-06-13 07:05:03,861] A new study created in memory with name: TSP_Hyperparameter_Optimization


Rozpoczynam optymalizację hiperparametrów...
Liczba prób: 100
Problem: TSP z 50 punktami


  0%|          | 0/100 [00:00<?, ?it/s]

[I 2025-06-13 07:05:14,630] Trial 0 finished with value: 5.862820198400066 and parameters: {'n_ants': 47, 'pheromone_reward_factor': 628.9060773061261, 'negative_pheromone_scaling': 0.5365564033222369, 'initial_rate': 0.06893623994973778, 'alpha': 2.674314379580815, 'beta': 3.352984880412896, 'gamma': 1.7727228267991106, 'rho_pos': 0.2520207912267887, 'rho_neg': 0.212706894305849, 'n_reinforce': 16, 'elite_boost': False}. Best is trial 0 with value: 5.862820198400066.


D:\Studia\semestr8\ioio\antmaxxing\discrete\dual_pheromone_tsp.py:238: RuntimeWarning: invalid value encountered in divide
  probabilities /= probabilities.sum()


...

[W 2025-06-13 07:21:47,406] Trial 1 is omitted in visualization because its objective value is inf or nan.
[W 2025-06-13 07:21:47,406] Trial 2 is omitted in visualization because its objective value is inf or nan.
[W 2025-06-13 07:21:47,407] Trial 3 is omitted in visualization because its objective value is inf or nan.
[W 2025-06-13 07:21:47,408] Trial 6 is omitted in visualization because its objective value is inf or nan.
[W 2025-06-13 07:21:47,408] Trial 38 is omitted in visualization because its objective value is inf or nan.
[W 2025-06-13 07:21:47,409] Trial 74 is omitted in visualization because its objective value is inf or nan.
[W 2025-06-13 07:21:47,409] Trial 93 is omitted in visualization because its objective value is inf or nan.


[I 2025-06-13 07:21:47,384] Trial 99 finished with value: 6.145981150457216 and parameters: {'n_ants': 59, 'pheromone_reward_factor': 305.4919984699597, 'negative_pheromone_scaling': 0.22524487234233548, 'initial_rate': 0.25201043354225744, 'alpha': 0.11797498589961086, 'beta': 3.4990762557727244, 'gamma': 3.5530992631054157, 'rho_pos': 0.47656201826444045, 'rho_neg': 0.13254173916928422, 'n_reinforce': 9, 'elite_boost': True}. Best is trial 60 with value: 5.598646560104341.

WYNIKI OPTYMALIZACJI
Najlepsza wartość: 5.598647
Najlepsze parametry:
  n_ants: 98
  pheromone_reward_factor: 474.7467907778399
  negative_pheromone_scaling: 0.4034087943529212
  initial_rate: 0.27847026059984126
  alpha: 1.0549363994873961
  beta: 2.810311804082339
  gamma: 3.0220761906943014
  rho_pos: 0.47002045095853295
  rho_neg: 0.2833240982517737
  n_reinforce: 10
  elite_boost: True

Liczba zakończonych prób: 100
Liczba prób z błędami: 0

Tworzenie wykresów...


[W 2025-06-13 07:21:48,513] Trial 1 is omitted in visualization because its objective value is inf or nan.
[W 2025-06-13 07:21:48,513] Trial 2 is omitted in visualization because its objective value is inf or nan.
[W 2025-06-13 07:21:48,514] Trial 3 is omitted in visualization because its objective value is inf or nan.
[W 2025-06-13 07:21:48,514] Trial 6 is omitted in visualization because its objective value is inf or nan.
[W 2025-06-13 07:21:48,515] Trial 38 is omitted in visualization because its objective value is inf or nan.
[W 2025-06-13 07:21:48,516] Trial 74 is omitted in visualization because its objective value is inf or nan.
[W 2025-06-13 07:21:48,516] Trial 93 is omitted in visualization because its objective value is inf or nan.



DODATKOWA ANALIZA
Top 10 najlepszych wyników:
 number    value
     60 5.598647
     89 5.598647
     79 5.603964
     95 5.611343
     61 5.613365
     98 5.613365
     96 5.625213
     43 5.634614
     62 5.634614
     63 5.634614

Korelacje parametrów z wartością celu:


ValueError: could not convert string to float: 'COMPLETE'